In [1]:
# importing libraries
import numpy as np
import pandas as pd
import pydub

from IPython.display import Audio
from keras.layers import Dense, LSTM, LeakyReLU
from keras.models import Sequential, load_model
from scipy.io.wavfile import read, write

C:\Users\hp\Anaconda3\lib\site-packages\h5py\__init__.py:34: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
# converting mp3 file to wav file
sound = pydub.AudioSegment.from_mp3("Numb_piano.mp3")
sound.export("Numb.wav", format="wav")
sound = pydub.AudioSegment.from_mp3("Eminem.mp3")
sound.export("Eminem.wav", format="wav")

<_io.BufferedRandom name='Eminem.wav'>

In [3]:
# loading the wav files
rate, music1 = read('Numb.wav')
rate, music2 = read('Eminem.wav')

In [4]:
# taking only some part of the songs and converting to a dataframe
music1 = pd.DataFrame(music1[0:400000, :])
music2 = pd.DataFrame(music2[0:400000, :])

In [5]:
# function to create train data by shifting the music data 
def create_train_dataset(df, look_back):
    dataX1, dataX2 , dataY1 , dataY2 = [],[],[],[]
    for i in range(len(df)-look_back-1):
        dataX1.append(df.iloc[i : i + look_back, 0].values)
        dataX2.append(df.iloc[i : i + look_back, 1].values)
        dataY1.append(df.iloc[i + look_back, 0])
        dataY2.append(df.iloc[i + look_back, 1])
    return np.array(dataX1), np.array(dataX2), np.array(dataY1), np.array(dataY2)

In [6]:
X1 , X2, y1 , y2 = create_train_dataset(pd.concat([music1.iloc[0 : 160000, :],music2.iloc[0 : 160000, :]], axis=0), 3)

In [7]:
print(X1.shape)
print(X2.shape)
print(y1.shape)
print(y2.shape)

(319996, 3)
(319996, 3)
(319996,)
(319996,)


In [8]:
# function to create train data by shifting the music data
def create_test_data(df, look_back):
    dataX1, dataX2 = [], []
    for i in range(len(df)-look_back-1):
        dataX1.append(df.iloc[i : i + look_back, 0].values)
        dataX2.append(df.iloc[i : i + look_back, 1].values)
        
    return np.array(dataX1), np.array(dataX2)

In [12]:
test1, test2 = create_test_data(pd.concat([music1.iloc[160001 : 400000, :],music2.iloc[160001 : 400000, :]], axis=0), 3)

In [13]:
X1 = X1.reshape((-1, 1, 3))
X2 = X2.reshape((-1, 1, 3))

In [14]:
# LSTM Model for channel 1 of the music data
rnn1 = Sequential()
rnn1.add(LSTM(units=100, activation='linear', input_shape=(None, 3)))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=50, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=25, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=12, activation='linear'))
rnn1.add(LeakyReLU())
rnn1.add(Dense(units=1, activation='linear'))
rnn1.add(LeakyReLU())

rnn1.compile(optimizer='adam', loss='mean_squared_error')
rnn1.fit(X1, y1, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 16s 51us/step - loss: 71782.8985
Epoch 2/20
319996/319996 [==============================] - 16s 49us/step - loss: 11343.5527
Epoch 3/20
319996/319996 [==============================] - 16s 49us/step - loss: 8850.1695
Epoch 4/20
319996/319996 [==============================] - 16s 50us/step - loss: 8527.8633
Epoch 5/20
319996/319996 [==============================] - 16s 50us/step - loss: 7964.7294
Epoch 6/20
319996/319996 [==============================] - 16s 50us/step - loss: 7980.3369
Epoch 7/20
319996/319996 [==============================] - 16s 50us/step - loss: 7850.4572
Epoch 8/20
319996/319996 [==============================] - 16s 50us/step - loss: 7798.8527
Epoch 9/20
319996/319996 [==============================] - 16s 50us/step - loss: 7722.5404
Epoch 10/20
319996/319996 [==============================] - 16s 50us/step - loss: 7665.1978
Epoch 11/20
319996/319996 [==============================] - 17s 53us/step - 

In [15]:
# LSTM Model for channel 2 of the music data
rnn2 = Sequential()
rnn2.add(LSTM(units=100, activation='linear', input_shape=(None, 3)))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=50, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=25, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=12, activation='linear'))
rnn2.add(LeakyReLU())
rnn2.add(Dense(units=1, activation='linear'))
rnn2.add(LeakyReLU())

rnn2.compile(optimizer='adam', loss='mean_squared_error')
rnn2.fit(X2, y2, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 18s 55us/step - loss: 276325.9465
Epoch 2/20
319996/319996 [==============================] - 16s 51us/step - loss: 31115.2845
Epoch 3/20
319996/319996 [==============================] - 16s 51us/step - loss: 17128.3895
Epoch 4/20
319996/319996 [==============================] - 16s 50us/step - loss: 14180.5239
Epoch 5/20
319996/319996 [==============================] - 17s 52us/step - loss: 13855.1637
Epoch 6/20
319996/319996 [==============================] - 16s 50us/step - loss: 13644.9823
Epoch 7/20
319996/319996 [==============================] - 17s 53us/step - loss: 13215.3744
Epoch 8/20
319996/319996 [==============================] - 16s 51us/step - loss: 13012.8440
Epoch 9/20
319996/319996 [==============================] - 16s 51us/step - loss: 12940.2967
Epoch 10/20
319996/319996 [==============================] - 16s 51us/step - loss: 12668.6555
Epoch 11/20
319996/319996 [==============================] - 16s 51u

In [16]:
# saving LSTM models
rnn1.model.save('rnn1.h5')
rnn2.model.save('rnn2.h5')

C:\Users\hp\Anaconda3\lib\site-packages\keras\engine\sequential.py:109: UserWarning: `Sequential.model` is deprecated. `Sequential` is a subclass of `Model`, you can just use your `Sequential` instance directly.
  warnings.warn('`Sequential.model` is deprecated. '


In [17]:
# loading the saved models
rnn1 = load_model('rnn1.h5')
rnn2 = load_model('rnn2.h5')

In [18]:
# making predictions for channel 1 and channel 2
pred_rnn1 = rnn1.predict(test1.reshape(-1, 1, 3))
pred_rnn2 = rnn2.predict(test2.reshape(-1, 1, 3))

In [19]:
# reshaping the data for input to ANN
X1 = X1.reshape((-1, 3))
X2 = X2.reshape((-1, 3))

In [20]:
# ANN Model for channel 1 of the music data
ann1 = Sequential()
ann1.add(Dense(units=100, activation='linear', input_dim=3))
ann1.add(LeakyReLU())
ann1.add(Dense(units=50, activation='linear'))
ann1.add(LeakyReLU())
ann1.add(Dense(units=25, activation='linear'))
ann1.add(LeakyReLU())
ann1.add(Dense(units=12, activation='linear'))
ann1.add(LeakyReLU())
ann1.add(Dense(units=1, activation='linear'))
ann1.add(LeakyReLU())

ann1.compile(optimizer='adam', loss='mean_squared_error')
ann1.fit(X1, y1, epochs = 20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 8s 26us/step - loss: 45080.3955
Epoch 2/20
319996/319996 [==============================] - 7s 21us/step - loss: 8048.2210
Epoch 3/20
319996/319996 [==============================] - 7s 23us/step - loss: 7692.2827
Epoch 4/20
319996/319996 [==============================] - 7s 22us/step - loss: 7594.1525
Epoch 5/20
319996/319996 [==============================] - 7s 22us/step - loss: 7504.7117
Epoch 6/20
319996/319996 [==============================] - 7s 22us/step - loss: 7388.9779
Epoch 7/20
319996/319996 [==============================] - 7s 22us/step - loss: 7250.6292
Epoch 8/20
319996/319996 [==============================] - 7s 21us/step - loss: 7354.2749
Epoch 9/20
319996/319996 [==============================] - 7s 21us/step - loss: 7202.1316
Epoch 10/20
319996/319996 [==============================] - 7s 20us/step - loss: 7170.1706
Epoch 11/20
319996/319996 [==============================] - 7s 21us/step - loss: 7258.1

In [21]:
# ANN Model for channel 2 of the music data
ann2 = Sequential()
ann2.add(Dense(units=100, activation='linear', input_dim=3))
ann2.add(LeakyReLU())
ann2.add(Dense(units=50, activation='linear'))
ann2.add(LeakyReLU())
ann2.add(Dense(units=25, activation='linear'))
ann2.add(LeakyReLU())
ann2.add(Dense(units=12, activation='linear'))
ann2.add(LeakyReLU())
ann2.add(Dense(units=1, activation='linear'))
ann2.add(LeakyReLU())

ann2.compile(optimizer='adam', loss='mean_squared_error')
ann2.fit(X2, y2, epochs=20, batch_size=100)

Epoch 1/20
319996/319996 [==============================] - 8s 26us/step - loss: 151498.0129
Epoch 2/20
319996/319996 [==============================] - 7s 21us/step - loss: 14465.1618
Epoch 3/20
319996/319996 [==============================] - 7s 21us/step - loss: 13248.9161
Epoch 4/20
319996/319996 [==============================] - 7s 21us/step - loss: 12575.4529
Epoch 5/20
319996/319996 [==============================] - 7s 21us/step - loss: 12805.5325
Epoch 6/20
319996/319996 [==============================] - 7s 22us/step - loss: 12275.9154
Epoch 7/20
319996/319996 [==============================] - 7s 22us/step - loss: 11356.0223
Epoch 8/20
319996/319996 [==============================] - 7s 22us/step - loss: 12185.3581
Epoch 9/20
319996/319996 [==============================] - 8s 25us/step - loss: 11556.3906
Epoch 10/20
319996/319996 [==============================] - 8s 25us/step - loss: 11734.5228
Epoch 11/20
319996/319996 [==============================] - 7s 22us/step - lo

In [22]:
# saving ANN models
ann1.model.save('ann1.h5')
ann2.model.save('ann2.h5')

C:\Users\hp\Anaconda3\lib\site-packages\keras\engine\sequential.py:109: UserWarning: `Sequential.model` is deprecated. `Sequential` is a subclass of `Model`, you can just use your `Sequential` instance directly.
  warnings.warn('`Sequential.model` is deprecated. '


In [23]:
# loading saved ANN models
ann1 = load_model('ann1.h5')
ann2 = load_model('ann2.h5')

In [24]:
# making predictions for channel 1 and channel 2
pred_ann1 = ann1.predict(test1)
pred_ann2 = ann2.predict(test2)

In [25]:
# saving the ANN predicitons in wav format
write('pred_ann.wav', rate, pd.concat([pd.DataFrame(pred_ann1.astype('int16')), pd.DataFrame(pred_ann2.astype('int16'))], axis=1).values)

In [26]:
# saving the LSTM predicitons in wav format
write('pred_rnn.wav', rate, pd.concat([pd.DataFrame(pred_rnn1.astype('int16')), pd.DataFrame(pred_rnn2.astype('int16'))], axis=1).values)

In [28]:
# saving the original music in wav format
write('original.wav',rate, pd.concat([music1.iloc[160001 : 400000, :], music2.iloc[160001 : 400000, :]], axis=0).values)

In [29]:
Audio("pred_ann.wav")

In [32]:
Audio("pred_rnn.wav")

In [31]:
Audio("original.wav")